In [343]:
import pandas as pd
import numpy as np
import os
import re
import string
import xml.etree.ElementTree as ET
import json
import random
from collections import defaultdict

# Exploring

In [172]:
positionings = pd.read_csv("positionings.csv", delimiter='\t')

In [173]:
positionings_6_columns = positionings.iloc[:, :6]

In [174]:
positionings_6_columns.head()

wsj_section   wsj_doc    DcOffset                                Label1  \
0           14  wsj_1485    320..324                 Expansion.Conjunction   
1           14  wsj_1461    402..406                 Expansion.Conjunction   
2           14  wsj_1461    782..785  Comparison.Concession.Arg2-as-denier   
3           14  wsj_1461  1123..1125                 Comparison.Similarity   
4           14  wsj_1416    331..343              Contingency.Cause.Result   

  Label2         DcRaw  
0    NaN          also  
1    NaN          with  
2    NaN           but  
3    NaN            as  
4    NaN  consequently

In [175]:
positionings_6_columns.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 24238 entries, 0 to 24237
Data columns (total 6 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   wsj_section  24238 non-null  int64 
 1   wsj_doc      24238 non-null  object
 2   DcOffset     24238 non-null  object
 3   Label1       24238 non-null  object
 4   Label2       1167 non-null   object
 5   DcRaw        24238 non-null  object
dtypes: int64(1), object(5)
memory usage: 1.1+ MB


In [179]:
# Identified wrong entry in the dataframe where there is multiple offsets but only one connector
dd = positionings_6_columns[positionings_6_columns['DcOffset'].str.contains(';')].copy()
filtered_df = dd[dd['DcRaw'].apply(lambda x: len(x.split()) == 1)]
filtered_df.head()

wsj_section   wsj_doc               DcOffset                Label1  \
935           14  wsj_1469  6474..6486;6497..6501  Temporal.Synchronous   

                       Label2 DcRaw  
935  Contingency.Cause.Reason  when

In [180]:
#modify row 935 to only have one offset
positionings_6_columns.loc[935, "DcOffset"] = "6497..6501"
positionings_6_columns.loc[935]

wsj_section                          14
wsj_doc                        wsj_1469
DcOffset                     6497..6501
Label1             Temporal.Synchronous
Label2         Contingency.Cause.Reason
DcRaw                              when
Name: 935, dtype: object

In [181]:
filtered_df = positionings_6_columns[positionings_6_columns['DcOffset'].str.count(';') >= 2]
filtered_df

wsj_section   wsj_doc                          DcOffset  \
3738            21  wsj_2155  3107..3115;3152..3155;3160..3164   
10477           10  wsj_1002  5828..5836;5877..5880;5885..5889   
18790           11  wsj_1187  4899..4907;4965..4968;4979..4983   

                      Label1 Label2              DcRaw  
3738   Expansion.Conjunction    NaN  not only but also  
10477  Expansion.Conjunction    NaN  not only but also  
18790  Expansion.Conjunction    NaN  not only but also

In [182]:
len(positionings_6_columns)

24238

# Preprocess

In [453]:
positionings_6_columns_clean = positionings_6_columns.copy()
#cloning the DcRaw column for preserving statistics purposes 
positionings_6_columns_clean['DcRaw_og'] = positionings_6_columns_clean['DcRaw'].copy()

In [454]:
positionings_6_columns_clean

wsj_section   wsj_doc    DcOffset  \
0               14  wsj_1485    320..324   
1               14  wsj_1461    402..406   
2               14  wsj_1461    782..785   
3               14  wsj_1461  1123..1125   
4               14  wsj_1416    331..343   
...            ...       ...         ...   
24233           24  wsj_2404  2939..2949   
24234           24  wsj_2441    880..884   
24235           24  wsj_2441    866..873   
24236           24  wsj_2436    421..424   
24237           24  wsj_2436  1186..1191   

                                     Label1 Label2         DcRaw      DcRaw_og  
0                     Expansion.Conjunction    NaN          also          also  
1                     Expansion.Conjunction    NaN          with          with  
2      Comparison.Concession.Arg2-as-denier    NaN           but           but  
3                     Comparison.Similarity    NaN            as            as  
4                  Contingency.Cause.Result    NaN  consequently  consequently  
...                                     ...    ...           ...           ...  
24233                 Expansion.Conjunction    NaN    separately    separately  
24234                 Expansion.Conjunction    NaN          also          also  
24235              Contingency.Cause.Reason    NaN       because       because  
24236  Comparison.Concession.Arg2-as-denier    NaN           but           but  
24237                  Temporal.Synchronous    NaN         while         while  

[24238 rows x 7 columns]

In [471]:
filtered_df = positionings_6_columns_clean[positionings_6_columns_clean['Label1'].str.endswith(('Reason+SpeechAct'), na=False)]
filtered_df

wsj_section   wsj_doc    DcOffset  \
17207           15  wsj_1560  1437..1440   

                                             Label1 Label2 DcRaw DcRaw_og  
17207  Contingency.Cause+SpeechAct.Reason+SpeechAct    NaN   but      but

## Cropping the third label

In [290]:
# crop the third label in Label1 column
positionings_6_columns_clean['Label1'] = positionings_6_columns_clean['Label1'].str.split('.').str[1]
positionings_6_columns_clean['Label2'] = positionings_6_columns_clean['Label2'].str.split('.').str[1]
positionings_6_columns_unsplitted = positionings_6_columns_clean.copy()
positionings_6_columns_clean[['Label1','Label2']]

Label1 Label2
0      Conjunction    NaN
1      Conjunction    NaN
2       Concession    NaN
3       Similarity    NaN
4            Cause    NaN
...            ...    ...
24233  Conjunction    NaN
24234  Conjunction    NaN
24235        Cause    NaN
24236   Concession    NaN
24237  Synchronous    NaN

[24238 rows x 2 columns]

In [292]:
positionings_6_columns_clean["Label1"].nunique()

21

In [293]:
dd = positionings_6_columns[positionings_6_columns['DcOffset'].str.contains(';')].copy()
len(dd)

123

In [294]:
positionings_6_columns_clean[positionings_6_columns_clean['DcRaw'].str.contains(' ')]

wsj_section   wsj_doc    DcOffset           Label1 Label2        DcRaw  \
5               14  wsj_1416  1221..1228      Conjunction    NaN      in fact   
12              14  wsj_1416  2452..2463       Concession    NaN  even though   
16              14  wsj_1424    748..759    Instantiation    NaN  for example   
20              14  wsj_1424  2806..2812            Cause    NaN       due to   
21              14  wsj_1424  2886..2896      Synchronous    NaN   as long as   
...            ...       ...         ...              ...    ...          ...   
24145           24  wsj_2428  7083..7090  Level-of-detail    NaN      in that   
24153           24  wsj_2428  8475..8486      Conjunction    NaN  in addition   
24167           24  wsj_2417    807..818       Concession    NaN  even though   
24184           24  wsj_2417  3986..3997      Conjunction    NaN  in addition   
24203           24  wsj_2417  8272..8283       Concession    NaN  even though   

          DcRaw_og  
5          in fact  
12     even though  
16     for example  
20          due to  
21      as long as  
...            ...  
24145      in that  
24153  in addition  
24167  even though  
24184  in addition  
24203  even though  

[1612 rows x 7 columns]

In [295]:
# step 1 split the offset column
def splitting_multiple_offsets(raw_data_frame, is_cz = False):
    # New row splitting approach
    split_rows = raw_data_frame[raw_data_frame['DcRaw'].str.contains(' ')].copy()
    split_rows['DcRaw'] = split_rows['DcRaw'].str.split()

    # first step is splitting all the rows that have ";"" and then make 1 pass to make all of the dataframe have 1 offset
    split_rows['DcOffset'] = split_rows['DcOffset'].apply(lambda x: x.split(';') if ';' in x else [x]) 
    dfs = []
    orignal_indicies = []
    for index, row in split_rows.iterrows():
        # we will first work on only the rows that have multiple offsets (2 and 3 offsets seperated by ";")
            if len(row["DcOffset"]) > 1:
                # save the row data
                if not is_cz:    
                    wsj_section = row['wsj_section']
                    wsj_doc = row['wsj_doc']
                    label1 = row['Label1']
                    label2 = row['Label2']
                    dcRaw = row["DcRaw_og"]
                else:
                    label1 = row['Label1']
                # initialize helpful variables
                word_pointer = 0
                connectors = row["DcRaw"]
                # iterate over offsets
                for offset in row["DcOffset"]:
                    start_offset = int(offset.split("..")[0])
                    end_offset = int(offset.split("..")[1])
                    # list to store the connectors in their respective offset
                    words_per_offset = []
                    # variable to check if you exceeded the offet length
                    offset_length_count = start_offset
                    # loop over the connectors in the row and see if adding the length of the word to the count will fit 
                    while word_pointer < len(connectors):
                        if offset_length_count + len(connectors[word_pointer]) <= end_offset:
                            # if it does add it to the list and point to the next word and update counter
                            words_per_offset.append(connectors[word_pointer])                                                
                            offset_length_count += len(connectors[word_pointer]) + 1 # considering the space length
                            word_pointer += 1

                        else:
                            # add the list to the offset in a single row
                            if not is_cz:
                                row_adjusted = {'wsj_section': wsj_section,
                                                'wsj_doc': wsj_doc,
                                                'DcOffset': offset,
                                                'Label1': label1,
                                                'Label2': label2,
                                                'DcRaw_og': dcRaw,
                                                'DcRaw': ' '.join(words_per_offset)}
                            else:
                                row_adjusted = {'DcOffset': offset,
                                                'Label1': label1,
                                                'DcRaw': ' '.join(words_per_offset)}

                            dfs.append(row_adjusted)
                            words_per_offset = []
                            break

                    # if not empty add the last word in the list
                    if words_per_offset:
                        if not is_cz:
                                row_adjusted = {'wsj_section': wsj_section,
                                                'wsj_doc': wsj_doc,
                                                'DcOffset': offset,
                                                'Label1': label1,
                                                'Label2': label2,
                                                'DcRaw_og': dcRaw,
                                                'DcRaw': ' '.join(words_per_offset)}
                        else:
                            row_adjusted = {'DcOffset': offset,
                                            'Label1': label1,
                                            'DcRaw': ' '.join(words_per_offset)}

                        dfs.append(row_adjusted)
            # If it's only 1 offset leave it as is in the df and deal with it in the second pass(save the indicies and append it in the end)
            else:
                orignal_indicies.append(index)
                
    # dataframe with all the adjusted rows that have ;
    result_df = pd.DataFrame(dfs)

    # Add the 1 offset rows
    for index in orignal_indicies:
        result_df = pd.concat([result_df, raw_data_frame.iloc[index].to_frame().T] , ignore_index=True)

    return result_df

In [296]:
result_df = splitting_multiple_offsets(positionings_6_columns_clean)
result_df

wsj_section   wsj_doc    DcOffset           Label1 Label2  \
0             14  wsj_1424  4740..4744      Conjunction    NaN   
1             14  wsj_1424  4790..4793      Conjunction    NaN   
2             14  wsj_1457  4597..4612         Contrast    NaN   
3             14  wsj_1457  4672..4684         Contrast    NaN   
4             14  wsj_1467  4780..4786      Disjunction    NaN   
...          ...       ...         ...              ...    ...   
1733          24  wsj_2428  7083..7090  Level-of-detail    NaN   
1734          24  wsj_2428  8475..8486      Conjunction    NaN   
1735          24  wsj_2417    807..818       Concession    NaN   
1736          24  wsj_2417  3986..3997      Conjunction    NaN   
1737          24  wsj_2417  8272..8283       Concession    NaN   

                          DcRaw_og            DcRaw  
0                         both and             both  
1                         both and              and  
2     on the one hand on the other  on the one hand  
3     on the one hand on the other     on the other  
4                        either or           either  
...                            ...              ...  
1733                       in that          in that  
1734                   in addition      in addition  
1735                   even though      even though  
1736                   in addition      in addition  
1737                   even though      even though  

[1738 rows x 7 columns]

In [297]:
# step 2 split the DcRaw column

# now you have a dataframe, for each row you only have 1 offset but can have multiple consecutive connectors within this offset
# break it down even more to have one word in DcRaw per row.
            
# subsequent connectors case, adjust the offseet such that num1..num1 + len(word) and num1 + len(word)+1..num2 +...
# Function to break down entries with more than one word.
def break_down_row(row, is_cz = False):
    if len(row['DcRaw'].split()) > 1:
        words = row['DcRaw'].split()
        start_offset = int(row['DcOffset'].split('..')[0])
        end_offset = int(row['DcOffset'].split('..')[1])
        offset_increment = (end_offset - start_offset) // len(words)
        new_rows = []
        current_offset = start_offset
        for word in words:
            if not is_cz:
                new_rows.append({
                    'wsj_section': row['wsj_section'],
                    'wsj_doc': row['wsj_doc'],
                    'DcOffset': f"{current_offset}..{current_offset + len(word)}",
                    'Label1': row['Label1'],
                    'Label2': row['Label2'],
                    'DcRaw_og': row['DcRaw_og'],
                    'DcRaw': word
                })
            else:
                new_rows.append({
                    'DcOffset': f"{current_offset}..{current_offset + len(word)}",
                    'Label1': row['Label1'],
                    'DcRaw': word
                })
                
            current_offset += len(word) + 1
        return new_rows
    else:
        return [row.to_dict()]

# Apply the function to each row and concatenate the results
new_rows = []
for _, row in result_df.iterrows():
    new_rows.extend(break_down_row(row))

# Create a new DataFrame with the modified rows
splitted_rows_df = pd.DataFrame(new_rows)

# Reset index
splitted_rows_df.reset_index(drop=True, inplace=True)
splitted_rows_df.head()

wsj_section   wsj_doc    DcOffset       Label1 Label2  \
0           14  wsj_1424  4740..4744  Conjunction    NaN   
1           14  wsj_1424  4790..4793  Conjunction    NaN   
2           14  wsj_1457  4597..4599     Contrast    NaN   
3           14  wsj_1457  4600..4603     Contrast    NaN   
4           14  wsj_1457  4604..4607     Contrast    NaN   

                       DcRaw_og DcRaw  
0                      both and  both  
1                      both and   and  
2  on the one hand on the other    on  
3  on the one hand on the other   the  
4  on the one hand on the other   one

In [298]:
# step 3 replace rows that got splitted with the splitted rows
def replace_splitted_rows(og_df, new_splitted_rows, is_cz = False):
    # Drop the rows that were extracted for splitting
    for index, row in og_df.iterrows():
        # Check if the 'DcRaw' column contains a space
        if ' ' in row['DcRaw']:
            # Remove the row
            og_df.drop(index, inplace=True)
    # Reset the index after removing rows
    og_df.reset_index(drop=True, inplace=True)
    # Concatenate the splitted_rows_df with positionings_6_columns_clean
    og_df = pd.concat([og_df, new_splitted_rows], ignore_index=True)
    # Sort the DataFrame by 'wsj_doc'
    if not is_cz:
        og_df.sort_values(by='wsj_doc', inplace=True)
    # Reset the index
    og_df.reset_index(drop=True, inplace=True)
    return og_df

In [299]:
positionings_6_columns_clean = replace_splitted_rows(positionings_6_columns_clean, splitted_rows_df)
positionings_6_columns_clean

wsj_section   wsj_doc    DcOffset        Label1           Label2  \
0                0  wsj_0003  3522..3525   Conjunction              NaN   
1                0  wsj_0003  3904..3907    Concession              NaN   
2                0  wsj_0003  1440..1443   Conjunction              NaN   
3                0  wsj_0003    534..542      Contrast              NaN   
4                0  wsj_0003    284..288  Cause+Belief  Level-of-detail   
...            ...       ...         ...           ...              ...   
26308           24  wsj_2454    558..561   Conjunction              NaN   
26309           24  wsj_2454    469..471   Synchronous              NaN   
26310           24  wsj_2454    465..468   Conjunction              NaN   
26311           24  wsj_2454  4628..4633       Purpose              NaN   
26312           24  wsj_2454  1520..1523    Concession              NaN   

          DcRaw  DcRaw_og  
0           and       and  
1           but       but  
2           and       and  
3      although  although  
4          with      with  
...         ...       ...  
26308       and       and  
26309        as        as  
26310       and       and  
26311     order  in order  
26312       but       but  

[26313 rows x 7 columns]

## validity check


In [300]:
#result_df[["wsj_doc","DcOffset", "DcRaw"]].head(50)
filtered_df = positionings_6_columns[positionings_6_columns['DcRaw'].apply(lambda x: len(x.split(" ")) == 4)]
filtered_df

wsj_section   wsj_doc               DcOffset                 Label1  \
700             14  wsj_1464             1907..1923   Temporal.Synchronous   
1022             7  wsj_0748             1286..1302   Temporal.Synchronous   
1087             7  wsj_0742             7600..7617    Comparison.Contrast   
1176             7  wsj_0799  5809..5817;5878..5886  Expansion.Conjunction   
1223             7  wsj_0764             3031..3048    Comparison.Contrast   
...            ...       ...                    ...                    ...   
22766           16  wsj_1634             5097..5114    Comparison.Contrast   
23192           16  wsj_1642               276..293    Comparison.Contrast   
23355           16  wsj_1613               758..775    Comparison.Contrast   
23383           16  wsj_1693              989..1005   Temporal.Synchronous   
23803           24  wsj_2454               273..289   Temporal.Synchronous   

      Label2              DcRaw  
700      NaN   at the same time  
1022     NaN   at the same time  
1087     NaN  on the other hand  
1176     NaN  not only but also  
1223     NaN  on the other hand  
...      ...                ...  
22766    NaN  on the other hand  
23192    NaN  on the other hand  
23355    NaN  on the other hand  
23383    NaN   at the same time  
23803    NaN   at the same time  

[114 rows x 6 columns]

In [306]:
unique_labels = positionings_6_columns_clean['Label1'].unique()
# Create label_map
label_map = {label: idx + 1 for idx, label in enumerate(unique_labels)}
print(label_map)

{'Conjunction': 1, 'Concession': 2, 'Contrast': 3, 'Cause+Belief': 4, 'Asynchronous': 5, 'Cause': 6, 'Instantiation': 7, 'Condition': 8, 'Synchronous': 9, 'Substitution': 10, 'Disjunction': 11, 'Purpose': 12, 'Level-of-detail': 13, 'Manner': 14, 'Negative-condition': 15, 'Concession+SpeechAct': 16, 'Condition+SpeechAct': 17, 'Similarity': 18, 'Exception': 19, 'Equivalence': 20, 'Cause+SpeechAct': 21}


# Parsing the file

In [411]:
# sort the tokens and ids lists to training or testing or dev set depending on the folder number
def sort_data(folder_num, tokens_list, id_list, train_tokens, train_ids, test_tokens, test_ids, dev_tokens, dev_ids):
    folder_num = int(folder_num)
    if folder_num == 22:
        dev_tokens.append(tokens_list)
        dev_ids.append(id_list)
    elif folder_num == 23:
        test_tokens.append(tokens_list)
        test_ids.append(id_list)
    else:
        train_tokens.append(tokens_list)
        train_ids.append(id_list)

In [412]:
def convert_to_jsonl(tokens_list, ids_list, output_file):
    # Ensure the lengths of tokens_list and ids_list are the same
    if len(tokens_list) != len(ids_list):
        raise ValueError("The lengths of tokens_list and ids_list must be the same.")
    
    # Open the output file in write mode
    with open(output_file, 'w') as file:
        for tokens, ids in zip(tokens_list, ids_list):
                # Create a dictionary for each entry
                entry = {"tokens": tokens, "ner_tags": ids}
                # Convert the dictionary to a JSON string and write it to the file
                file.write(json.dumps(entry) + '\n')

In [413]:
def convert_to_json(tokens_list, ids_list, output_file):
    # Ensure the lengths of tokens_list and ids_list are the same
    if len(tokens_list) != len(ids_list):
        raise ValueError("The lengths of tokens_list and ids_list must be the same.")
    
    # Create a list to hold all entries
    entries = []
    for tokens, ids in zip(tokens_list, ids_list):
        # Create a dictionary for each entry
        entry = {"tokens": tokens, "ner_tags": ids}
        # Append each entry to the list
        entries.append(entry)
    
    # Save all entries as a JSON array in the output file
    with open(output_file, 'w') as file:
        json.dump(entries, file, indent=4)

In [414]:
# 0s and multiple labels for relation classification task
def check_offset_relation_recognition_task(word, offsets_labels, label_map, word_offset):
    # Check if the word is within any offset
    flag = 0
    for offset, label in offsets_labels:
        start, end = map(int, offset.split('..'))
        # adjust offset if there is punctuation
        if word[-1] in string.punctuation and flag == 0:
            #print(word_offset)
            #print(word)
            flag = 1
            word_offset = word_offset - 1
        if end == word_offset:
            # If the word is within an offset, replace it with the corresponding label
            if flag == 1:
                flag = 0
            return label_map[label]
    # If not within offset, replace the word with 0
    return 0

In [415]:
# only 0s and 1s for only connective detection task
def check_offset_connevtive_detection_task(word, offsets_labels, label_map, word_offset):
    # Check if the word is within any offset
    flag = 0
    for offset, label in offsets_labels:
        start, end = map(int, offset.split('..'))
        # adjust offset if there is punctuation
        if word[-1] in string.punctuation and flag == 0:
            #print(word_offset)
            #print(word)
            flag = 1
            word_offset = word_offset - 1
        if end == word_offset:
            # If the word is within an offset, replace it with the corresponding label
            if flag == 1:
                flag = 0
            return 1
    # If not within offset, replace the word with 0
    return 0

In [416]:
def parse_text(text, offsets_labels):
    processed_text = []
    current_word = ''  
    token_list =[]
    for current_position, char in enumerate(text):
        if char == ' ':  # Check if the character is a space(word delimiter)                
            # Process the current word
            if current_word != '':
                processed_text.append(check_offset_relation_recognition_task(current_word, offsets_labels, label_map, current_position))
                token_list.append(current_word)
            current_word = ''
            
        elif char == "\n": # another delimiter but we include it in our tokens list with id = 0
            if current_word != '':
                processed_text.append(check_offset_relation_recognition_task(current_word, offsets_labels, label_map, current_position))
                token_list.append(current_word)
                
            current_word = ''
            processed_text.append(0)
            token_list.append("\n")
            
        else:
            current_word += char
    # Process the last word 
    if current_word:
        processed_text.append(check_offset_relation_recognition_task(current_word, offsets_labels, label_map, current_position))
        token_list.append(current_word)
    return processed_text, token_list

In [417]:
    base_dir = './PDTB3.0_raw'
    # files_list to keep track of the iterated files
    files_list = [positionings_6_columns_clean["wsj_doc"][0]]
    # tuples of connectors offsets with their coressponding label
    connector_offsets_label = []
    folder_name = f"{positionings_6_columns_clean['wsj_section'][0]:02d}"
    file_name = positionings_6_columns_clean['wsj_doc'][0]
    folder_path = os.path.join(base_dir, folder_name)
    file_path = os.path.join(folder_path, file_name)
    count = 0
    
    # lists to store all the processed text and their respective tokens
    all_tokens_list = []
    all_parsed_text_list = []
    train_tokens = []
    train_ids = []
    test_tokens = []
    test_ids = []
    dev_tokens = []
    dev_ids = []
    
    for index, row in positionings_6_columns_clean.iterrows():
        file_name = row['wsj_doc']
        if file_name not in files_list:
            #if new file then we need to parse the previous one using the offset-label tuples we have.
            if os.path.exists(file_path):
                with open(file_path, 'r', encoding='latin-1') as file:
                    # Parse the text
                    text = file.read()
                    parsed_text, tokens_list = parse_text(text, connector_offsets_label)
                    all_tokens_list.append(tokens_list)
                    all_parsed_text_list.append(parsed_text)
                    # split and sort the data
                    sort_data(folder_name, tokens_list, parsed_text, train_tokens, train_ids, test_tokens, test_ids, dev_tokens, dev_ids)
                    # Reset the list for the new file
                    connector_offsets_label = []
                    connector_offsets_label.append((row['DcOffset'], row["Label1"]))
                    files_list.append(file_name)
            else:
                print(f"File not found: {file_path}")
                
            folder_name = f"{row['wsj_section']:02d}"
            folder_path = os.path.join(base_dir, folder_name)
            file_path = os.path.join(folder_path, file_name)
        else:
            # if iterating over the same file keep track of the offsets and their corresponding labels
            if not pd.isna(row['Label2']):
                # use label1_label2
                #connector_offsets_label.append((row['DcOffset'], f"{row['Label1']}_{row['Label2']}"))
                
                # use only label1 as the model only works on int ids cant use label1_label2
                connector_offsets_label.append((row['DcOffset'], f"{row['Label1']}"))
            else:
                connector_offsets_label.append((row['DcOffset'], f"{row['Label1']}"))

# last File parsing
if os.path.exists(file_path):
        with open(file_path, 'r', encoding='latin-1') as file:
            # Parse the text
            text = file.read()
            parsed_text, tokens_list = parse_text(text, connector_offsets_label)
            all_tokens_list.append(tokens_list)
            all_parsed_text_list.append(parsed_text)
            sort_data(folder_name, tokens_list, parsed_text, train_tokens, train_ids, test_tokens, test_ids, dev_tokens, dev_ids)

else:
        print(f"Last file not found: {file_path}")

0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6
6


## Partition articles into sentences by using line breaks

In [353]:
# Function to segment lists based on a line break
def segment_lists(tokens, ids):
    flat_tokens = [token for sublist in tokens for token in sublist]
    flat_ids = [id for sublist in ids for id in sublist]
    token_segments = []
    id_segments = []
    current_tokens = []
    current_ids = []
    for token, id in zip(flat_tokens, flat_ids):
        if token == "\n":
            if current_tokens:  
                token_segments.append(current_tokens)
                id_segments.append(current_ids)
                current_tokens = []
                current_ids = []
        else:
            current_tokens.append(token)
            current_ids.append(id)
    # Add the last segment if there's any
    if current_tokens:
        token_segments.append(current_tokens)
        id_segments.append(current_ids)

    return token_segments, id_segments

In [422]:
train_tokens_sentences, train_ids_sentences = segment_lists(train_tokens, train_ids)
test_tokens_sentences, test_ids_sentences = segment_lists(test_tokens, test_ids)
dev_tokens_sentences, dev_ids_sentences = segment_lists(dev_tokens, dev_ids)

# Statistics about the English dataset

## Map of Relation --> Connector

In [72]:
result = positionings_6_columns_unsplitted.groupby('Label1')['DcRaw'].value_counts().reset_index(name='count')
# Export to CSV file
result.to_csv('Labels_stats_en(relation --> connector).csv', index=False)

result

Label1             DcRaw  count
0      Arg1-as-cond               and     22
1      Arg1-as-cond              then      1
2    Arg1-as-denier          although    205
3    Arg1-as-denier             while    201
4    Arg1-as-denier            though     91
..              ...               ...    ...
359     Synchronous           however      1
360     Synchronous                if      1
361     Synchronous       if and when      1
362     Synchronous  in the meanwhile      1
363     Synchronous             still      1

[364 rows x 3 columns]

## Map Connector ---> Relation

In [46]:
def append_dict_token(token_dict, token, identifier):
     # If the token is not already in the token_counts dictionary, add it
    if token not in token_counts:
        token_counts[token] = {}
    # Increment the count for the corresponding identifier
    if identifier not in token_counts[token]:
        token_counts[token][identifier] = 1
    else:
        token_counts[token][identifier] += 1

In [448]:
# Initialize a defaultdict to store counts
token_counts = defaultdict(lambda: defaultdict(int))
unique_connectors = positionings_6_columns_clean["DcRaw"].unique()

# Initialize a variable to store tokens
token_buffer = []
# Iterate through tokens and identifiers simultaneously
for tokens, parsed_text in zip(all_tokens_list, all_parsed_text_list):
    for token, identifier in zip(tokens, parsed_text):
         # Check if the token is in the set of unique tokens
        if token in unique_connectors:
            # check if we have consecutive tokens and they have the same identifier then join tokens together
            if token_buffer and identifier == identifier_consecutive:
                # add it in a buffer after checking consecutive case
                token_buffer.append(token)
                identifier_consecutive = identifier
                
            # no buffer so this is a first encountered connector 
            elif not token_buffer:
                token_buffer.append(token)
                identifier_consecutive = identifier
                
            # case for consecutive connectors but with different identifiers
            else:
                # add the token_buffer
                token_previous = ' '.join(token_buffer)
                append_dict_token(token_counts, token_previous, identifier_consecutive)
                token_buffer = []
                # add the current token to a new empty buffer
                token_buffer.append(token)
                identifier_consecutive = identifier
        # non connector token and token_buffer is not empty, then append it to dict
        elif token_buffer:
            token = ' '.join(token_buffer) 
            token_buffer = []
            append_dict_token(token_counts, token, identifier_consecutive)    

for token, counts in token_counts.items():
    print("Special Token:", token)
    for identifier, count in counts.items():
        print("Identifier:", identifier, "Count:", count)

Special Token: of
Identifier: 0 Count: 17940
Identifier: 25 Count: 13
Identifier: 6 Count: 1
Special Token: once
Identifier: 0 Count: 70
Identifier: 5 Count: 47
Identifier: 10 Count: 1
Special Token: to
Identifier: 0 Count: 22248
Special Token: a
Identifier: 0 Count: 13856
Special Token: more than
Identifier: 0 Count: 411
Special Token: is
Identifier: 0 Count: 4872
Identifier: 16 Count: 1
Special Token: the
Identifier: 0 Count: 23086
Special Token: with
Identifier: 4 Count: 8
Identifier: 0 Count: 2868
Identifier: 16 Count: 111
Identifier: 7 Count: 50
Identifier: 9 Count: 7
Identifier: 1 Count: 41
Identifier: 17 Count: 6
Identifier: 11 Count: 2
Identifier: 10 Count: 1
Identifier: 3 Count: 1
Special Token: even
Identifier: 0 Count: 252
Special Token: that
Identifier: 0 Count: 6475
Identifier: 7 Count: 4
Identifier: 12 Count: 1
Identifier: 5 Count: 1
Identifier: 8 Count: 1
Special Token: later
Identifier: 0 Count: 82
Identifier: 8 Count: 77
Special Token: in
Identifier: 0 Count: 11017
Ide

Identifier: 10 Count: 33
Identifier: 26 Count: 1
Identifier: 11 Count: 4
Identifier: 5 Count: 3
Identifier: 14 Count: 1
Identifier: 20 Count: 1
Special Token: by the end of
Identifier: 0 Count: 28
Special Token: both
Identifier: 0 Count: 169
Identifier: 1 Count: 6
Special Token: previously
Identifier: 5 Count: 40
Identifier: 0 Count: 71
Special Token: on that
Identifier: 0 Count: 24
Special Token: as a result of an
Identifier: 0 Count: 2
Special Token: of an
Identifier: 0 Count: 162
Special Token: and by
Identifier: 0 Count: 21
Special Token: as well as to
Identifier: 0 Count: 7
Special Token: still of
Identifier: 0 Count: 1
Special Token: is in a
Identifier: 0 Count: 13
Special Token: one of the next
Identifier: 0 Count: 1
Special Token: is still
Identifier: 0 Count: 65
Special Token: time such an
Identifier: 0 Count: 1
Special Token: for by an
Identifier: 0 Count: 1
Special Token: of such
Identifier: 0 Count: 45
Special Token: is the only
Identifier: 0 Count: 12
Special Token: before

Identifier: 0 Count: 9
Special Token: of that
Identifier: 0 Count: 74
Special Token: in case
Identifier: 10 Count: 4
Special Token: in a case
Identifier: 0 Count: 8
Special Token: on the case by the end of the
Identifier: 0 Count: 1
Special Token: with the same
Identifier: 0 Count: 8
Special Token: therefore
Identifier: 12 Count: 23
Special Token: or less
Identifier: 0 Count: 7
Special Token: in by the end of the
Identifier: 0 Count: 1
Special Token: and in
Identifier: 0 Count: 50
Special Token: is in
Identifier: 0 Count: 77
Special Token: to less than
Identifier: 0 Count: 8
Special Token: from about
Identifier: 0 Count: 26
Special Token: due to
Identifier: 0 Count: 44
Identifier: 7 Count: 1
Special Token: of one
Identifier: 0 Count: 27
Special Token: upon
Identifier: 0 Count: 26
Identifier: 10 Count: 1
Identifier: 11 Count: 3
Identifier: 5 Count: 1
Special Token: as such
Identifier: 0 Count: 1
Special Token: is not the
Identifier: 0 Count: 12
Special Token: at any
Identifier: 0 Count:

Identifier: 0 Count: 2
Special Token: if not the
Identifier: 0 Count: 1
Special Token: not because of
Identifier: 0 Count: 3
Special Token: addition or
Identifier: 0 Count: 1
Special Token: instead of less
Identifier: 0 Count: 1
Special Token: with whether
Identifier: 0 Count: 2
Special Token: on the long
Identifier: 0 Count: 1
Special Token: of fact
Identifier: 0 Count: 2
Special Token: one for
Identifier: 0 Count: 5
Special Token: but because of the
Identifier: 0 Count: 1
Special Token: and less
Identifier: 0 Count: 11
Special Token: is next for
Identifier: 0 Count: 1
Special Token: more and more
Identifier: 0 Count: 6
Special Token: the end
Identifier: 0 Count: 4
Identifier: 1 Count: 1
Identifier: 16 Count: 1
Identifier: 23 Count: 1
Identifier: 12 Count: 1
Identifier: 8 Count: 2
Special Token: result in further
Identifier: 0 Count: 2
Special Token: of both the
Identifier: 0 Count: 9
Special Token: is not the time to
Identifier: 0 Count: 1
Special Token: is finally
Identifier: 0 Coun

Identifier: 0 Count: 5
Special Token: or more that
Identifier: 0 Count: 1
Special Token: is even
Identifier: 0 Count: 6
Special Token: both on
Identifier: 0 Count: 4
Special Token: neither the
Identifier: 0 Count: 6
Special Token: so long that the
Identifier: 0 Count: 1
Special Token: on the other
Identifier: 0 Count: 8
Special Token: in a previously
Identifier: 0 Count: 2
Special Token: a hand in
Identifier: 0 Count: 2
Special Token: much the
Identifier: 0 Count: 7
Special Token: in a given
Identifier: 0 Count: 3
Special Token: is about
Identifier: 0 Count: 23
Special Token: as in
Identifier: 0 Count: 12
Special Token: in more
Identifier: 0 Count: 7
Special Token: whether that is the
Identifier: 0 Count: 1
Special Token: that is the
Identifier: 0 Count: 7
Special Token: a result of the
Identifier: 0 Count: 5
Special Token: to further
Identifier: 0 Count: 15
Special Token: despite an
Identifier: 0 Count: 2
Special Token: that only a
Identifier: 0 Count: 5
Special Token: in more than
Id

...

Special Token: only at the
Identifier: 0 Count: 1
Special Token: of order to
Identifier: 0 Count: 1
Special Token: order a
Identifier: 0 Count: 1
Special Token: order is one of
Identifier: 0 Count: 1
Special Token: again with the same
Identifier: 0 Count: 1
Special Token: the other order
Identifier: 0 Count: 1
Special Token: at or by a
Identifier: 0 Count: 1
Special Token: any given
Identifier: 0 Count: 1
Special Token: just at the
Identifier: 0 Count: 1
Special Token: of the words
Identifier: 0 Count: 1
Special Token: on that one
Identifier: 0 Count: 1
Special Token: in other less
Identifier: 0 Count: 1
Special Token: time along with a
Identifier: 0 Count: 1
Special Token: time hence
Identifier: 0 Count: 1
Special Token: and finally
Identifier: 0 Count: 1
Special Token: beyond any
Identifier: 0 Count: 1
Special Token: where just
Identifier: 0 Count: 1
Special Token: the fact
Identifier: 0 Count: 2
Special Token: as no
Identifier: 0 Count: 2
Special Token: than that from
Identifier: 0 

Identifier: 0 Count: 1
Special Token: hand from
Identifier: 0 Count: 1
Special Token: but less time to
Identifier: 0 Count: 1
Special Token: earlier by
Identifier: 0 Count: 1
Special Token: not the end of the
Identifier: 0 Count: 1
Special Token: on hand because of a
Identifier: 0 Count: 1
Special Token: both for the
Identifier: 0 Count: 1
Special Token: at just
Identifier: 0 Count: 2
Special Token: no more a
Identifier: 0 Count: 1
Special Token: before in
Identifier: 0 Count: 2
Special Token: for example the
Identifier: 0 Count: 1
Special Token: as long as that for
Identifier: 0 Count: 1
Special Token: like any other
Identifier: 0 Count: 1
Special Token: no more or less than
Identifier: 0 Count: 1
Special Token: in a while the
Identifier: 0 Count: 1
Special Token: case than
Identifier: 0 Count: 1
Special Token: or one or more of
Identifier: 0 Count: 1
Special Token: and that
Identifier: 0 Count: 1
Special Token: in comparison
Identifier: 0 Count: 1
Special Token: where the only
Identi

Identifier: 0 Count: 1
Special Token: in until
Identifier: 0 Count: 1
Special Token: than an earlier one
Identifier: 0 Count: 1
Special Token: a later
Identifier: 0 Count: 1
Special Token: instead of the previously
Identifier: 0 Count: 1
Special Token: is due for a
Identifier: 0 Count: 1
Special Token: after other
Identifier: 0 Count: 1
Special Token: or separately
Identifier: 0 Count: 2
Special Token: due and
Identifier: 0 Count: 1
Special Token: or less of the
Identifier: 0 Count: 1
Special Token: due by
Identifier: 0 Count: 2
Special Token: and of an
Identifier: 0 Count: 1
Special Token: that then
Identifier: 0 Count: 2
Special Token: so much more
Identifier: 0 Count: 1
Special Token: short the
Identifier: 0 Count: 1
Special Token: about the only
Identifier: 0 Count: 2
Special Token: the addition to
Identifier: 0 Count: 1
Special Token: for or
Identifier: 0 Count: 1
Special Token: with then
Identifier: 0 Count: 1
Special Token: or otherwise depending on
Identifier: 0 Count: 1
Specia

Identifier: 0 Count: 1
Special Token: and from other
Identifier: 0 Count: 1
Special Token: the case that no
Identifier: 0 Count: 1
Special Token: that whatever the
Identifier: 0 Count: 1
Special Token: that where
Identifier: 0 Count: 1
Special Token: and accurately than
Identifier: 0 Count: 1
Special Token: than from
Identifier: 0 Count: 2
Special Token: much from
Identifier: 0 Count: 1
Special Token: now is to
Identifier: 0 Count: 1
Special Token: for the time to
Identifier: 0 Count: 1
Special Token: that even after
Identifier: 0 Count: 1
Special Token: at about one
Identifier: 0 Count: 1
Special Token: in contrast to the
Identifier: 0 Count: 1
Special Token: once that
Identifier: 0 Count: 1
Special Token: else is one to
Identifier: 0 Count: 1
Special Token: not yet a
Identifier: 0 Count: 1
Special Token: or as one
Identifier: 0 Count: 1
Special Token: for now to the
Identifier: 0 Count: 1
Special Token: so even
Identifier: 0 Count: 1
Special Token: as on the
Identifier: 0 Count: 1
Sp

Identifier: 0 Count: 1
Special Token: though only a
Identifier: 0 Count: 1
Special Token: still an
Identifier: 0 Count: 1
Special Token: of the time is
Identifier: 0 Count: 1
Special Token: on after
Identifier: 0 Count: 1
Special Token: not as an
Identifier: 0 Count: 1
Special Token: by of
Identifier: 0 Count: 1
Special Token: then of
Identifier: 0 Count: 2
Special Token: is one to
Identifier: 0 Count: 1
Special Token: or long
Identifier: 0 Count: 1
Special Token: only or
Identifier: 0 Count: 1
Special Token: when both the
Identifier: 0 Count: 1
Special Token: well or
Identifier: 0 Count: 1
Special Token: plus any further
Identifier: 0 Count: 1
Special Token: now than in the
Identifier: 0 Count: 1
Special Token: either on the
Identifier: 0 Count: 1
Special Token: or on a
Identifier: 0 Count: 1
Special Token: by such a
Identifier: 0 Count: 1
Special Token: of other more
Identifier: 0 Count: 1
Special Token: on of the
Identifier: 0 Count: 1
Special Token: of rather
Identifier: 0 Count: 1

In [151]:
df_dict = {}
for token, values in token_counts.items():
    identifiers = {}
    for identifier, count in values.items():
        identifiers[identifier] = int(count)
    df_dict[token] = identifiers

stats_english = pd.DataFrame.from_dict(df_dict, orient='index')

# Fill NaN values with 0
stats_english = stats_english.fillna(0)
stats_english = stats_english.astype(int)

# Create a new column by summing all columns except the first one
stats_english['sum_non_zero_tags'] = stats_english.iloc[:, 1:].sum(axis=1)
# Invert the dictionary to get a mapping from values to keys
inverted_dict = {v: k for k, v in label_map.items()}

# Rename the columns using the inverted dictionary
stats_english.rename(columns=inverted_dict, inplace=True)

stats_english.to_csv('Labels_stats_en(Connector ---> Relation).csv', index=True)

stats_english.head(50)

0  Arg1-as-subst  Arg1-as-denier  Succession  Arg2-as-cond  \
of             17907             13               1           0             0   
once              82              0               0          47             1   
to             22311              0               0           0             0   
a              13954              0               0           0             0   
more than        409              0               0           0             0   
is              4860              0               0           0             0   
the            23131              0               0           0             0   
with            2857              0               0           0             1   
even             258              0               0           0             0   
that            6590              0               0           1             0   
later             82              0               0           0             0   
in             11033              0               0           0             9   
more than a       27              0               0           0             0   
to the          1761              0               0           0             0   
is an             94              0               0           0             0   
about           1270              0               0           0             0   
before           190              0               0           0             0   
any              462              0               0           0             0   
is no             74              0               0           0             0   
now              525              0               0           0             0   
nor the            9              0               0           0             0   
of any            59              0               0           0             0   
on              3392              0               0           0             0   
of the          5212              0               0           0             0   
no               569              0               0           0             0   
on whether        11              0               0           0             0   
at              3191              0               0           0             0   
from the         971              0               0           0             0   
and the          849              0               0           0             0   
and            10829              0               0           0             0   
for the         1838              0               0           0             0   
in the          4291              0               0           0             0   
with a           519              0               0           0             0   
with the         890              0               0           0             0   
from            3455              1               0           0             0   
than             562              4               0           0             0   
is a             577              0               0           0             0   
at the           771              0               0           0             0   
for any           26              0               0           0             0   
by              3112              0               0           0            29   
that the        1288              0               0           0             0   
more             797              0               0           0             0   
than the         130              0               0           0             0   
and other        362              0               0           0             0   
is one of the     26              0               0           0             0   
like             330              0               0           0             0   
such as          346              0               0           0             0   
as              1646              0               7          23             0   
by the           932              0               

# Parsing Deutsch text files

In [153]:
# Auxiliary function to transform the xml file to a dict for easier handling
def xml_to_dict(element):
    result = {}
    if element.attrib:
        result.update({element.tag: element.attrib})
    if element.text and element.text.strip():  # Check if element has non-whitespace text content
        result.update({element.tag: element.text})
    for child in element:
        child_dict = xml_to_dict(child)
        if child.tag in result:
            # If the tag already exists, convert it to a list
            if not isinstance(result[child.tag], list):
                result[child.tag] = [result[child.tag]]
            result[child.tag].append(child_dict)
        else:
            result.update({child.tag: child_dict})
    return result

In [465]:
# loop over all files to get the Deutsch feature vector and targets
# Specify the directory path
folder_path = "./connectives"
# to keep track with statistics
token_count = defaultdict(lambda: defaultdict(int))

deutsch_tokens = []
deutsch_parsed_text = []
# Loop over all files in the folder
for filename in os.listdir(folder_path):
    # Check if the path is a file
    if os.path.isfile(os.path.join(folder_path, filename)):
        file_path = os.path.join(folder_path, filename)
        # Parse the XML file
        tree = ET.parse(file_path)
        root = tree.getroot()
        # Convert XML tree to dictionary
        xml_dict = xml_to_dict(root)
        
        # Extract tokens to a list
        tokens_dict = xml_dict['tokens']["token"]
        tokens_list = [token_dict["token"] for token_dict in tokens_dict]
        deutsch_tokens.append(tokens_list)
        # Get a list of relations
        list_of_relations = xml_dict["relations"]["relation"]
        
        # Initiate the parsed list with all zeroes
        parsed_text = [0] * len(tokens_list)
        # Get the ids of connective tokens
        for entry in list_of_relations:
            # Check if type is "explicit"
            if entry['relation']['type'] == 'explicit':
                # get current entry relation
                pdtb3_sense = entry['relation']['pdtb3_sense'].split('.')[-1]
                
                # Extract the id of the connective token
                connective_id = None
                if 'connective_token' in entry['connective_tokens']:
                    connective_token_entry = entry['connective_tokens']['connective_token']
                    if isinstance(connective_token_entry, list):
                        connective_id = [token['connective_token']['id'] for token in connective_token_entry]
                        for single_id in connective_id:
                            index = int(single_id) - 1
                            parsed_text[index] = label_map[pdtb3_sense]
                            token_count[pdtb3_sense][tokens_list[index].lower()] += 1
                                

                    else:
                        connective_id = entry['connective_tokens']['connective_token']['connective_token']['id']
                        index = int(connective_id) - 1
                        parsed_text[index] = label_map[pdtb3_sense]
                        token_count[pdtb3_sense][tokens_list[index].lower()] += 1
        
        deutsch_parsed_text.append(parsed_text)

In [467]:
for list_of_tokens in deutsch_tokens:
    for i, token in enumerate(list_of_tokens):
        if token == ".":
            print(deutsch_parsed_text[0][i])
            print(token)
    break

0
.
0
.
0
.
0
.
0
.
0
.
0
.
0
.
0
.
0
.
0
.


In [483]:
def split_lists_on_dot(tokens_list, parsed_text_list):
    # Initialize the resulting lists
    new_tokens_list = []
    new_parsed_text_list = []
    
    # Iterate through both lists simultaneously
    for tokens, parsed in zip(tokens_list, parsed_text_list):
        # Temporary lists to hold the current sublist
        temp_tokens = []
        temp_parsed = []
        
        for token, parsed_token in zip(tokens, parsed):
            if token == ".":
                # Append the current sublist and reset temporary lists
                new_tokens_list.append(temp_tokens)
                new_parsed_text_list.append(temp_parsed)
                
                temp_tokens = []
                temp_parsed = []
            else:
                # Continue building the current sublist
                temp_tokens.append(token)
                temp_parsed.append(parsed_token)
        
        # If there's any remaining items in temp lists, add them as well
        if temp_tokens:
            new_tokens_list.append(temp_tokens)
            new_parsed_text_list.append(temp_parsed)
    
    return new_tokens_list, new_parsed_text_list

splitted_deutsch_tokens, splitted_parsed_deutsch = split_lists_on_dot(deutsch_tokens, deutsch_parsed_text)

print(splitted_deutsch_tokens[4])
print(splitted_parsed_deutsch[4])

['Und', 'da', 'sieht', 'es', 'immer', 'schlechter', 'aus']
[1, 0, 0, 0, 0, 0, 0]


In [485]:
convert_to_jsonl(splitted_deutsch_tokens, splitted_parsed_deutsch, 'splitted_deutsch_data.jsonl')

## Split Deutsche dataset into training and testing and convert to jsonl format.

In [197]:
def split_data(tokens_list, ids_list, train_ratio=0.6):
    # Ensure the lengths of tokens_list and ids_list are the same
    if len(tokens_list) != len(ids_list):
        raise ValueError("The lengths of tokens_list and ids_list must be the same.")
    # Combine tokens and ids into a single list
    combined_data = list(zip(tokens_list, ids_list))
    # Shuffle the combined data to ensure randomness
    random.shuffle(combined_data)
    
    # Determine the split index
    split_index = int(len(combined_data) * train_ratio)
    
    # Split the data into training and testing sets
    train_data = combined_data[:split_index]
    test_data = combined_data[split_index:]
    # Unzip the training and testing data
    train_tokens, train_ids = zip(*train_data)
    test_tokens, test_ids = zip(*test_data)
    
    return list(train_tokens), list(train_ids), list(test_tokens), list(test_ids)

In [198]:
deutsch_train_tokens, deutsch_train_ids, deutsch_test_tokens, deutsch_test_ids = split_data(deutsch_tokens, deutsch_parsed_text)

In [199]:
# Convert the training data to JSONL
convert_to_jsonl(deutsch_train_tokens, deutsch_train_ids, 'train_deutsch_data.jsonl')

# Convert the testing data to JSONL
convert_to_jsonl(deutsch_test_tokens, deutsch_test_ids, 'test_deutsch_data.jsonl')

In [223]:
#same for french
french_train_tokens, french_train_ids, french_test_tokens, french_test_ids = split_data(all_processed_tokens_list_french, all_conn_list_french)

In [226]:
len(french_test_ids)

959

In [227]:
# Convert the training data to JSONL
convert_to_jsonl(french_train_tokens, french_train_ids, 'train_french_data.jsonl')

# Convert the testing data to JSONL
convert_to_jsonl(french_test_tokens, french_test_ids, 'test_french_data.jsonl')

# Deutsch Statistics
## Map of Relation --> Connector

In [200]:
# Prepare data for DataFrame
data = {'Sense': [], 'Connector Token': [], 'Count': []}
for sense, token_dict in token_count.items():
    for token, count in token_dict.items():
        data['Sense'].append(sense)
        data['Connector Token'].append(token)
        data['Count'].append(count)

# Create a DataFrame from the dictionary
deutsch_stat_df = pd.DataFrame(data)
with open('Deutsch(relation --> connector).txt', 'w') as f:
    f.write(deutsch_stat_df.to_string(index=False))
deutsch_stat_df

Sense Connector Token  Count
0       Conjunction             und    232
1       Conjunction            auch     30
2       Conjunction            aber      2
3       Conjunction              es      1
4       Conjunction         sondern      7
..              ...             ...    ...
181     Equivalence          worten      1
182     Equivalence     gleichfalls      1
183  Arg1-as-manner              so      1
184  Arg1-as-manner           somit      1
185  Arg1-as-detail        insofern      1

[186 rows x 3 columns]

In [158]:
# Initialize a defaultdict to store counts of identifiers for each special token
token_identifier_counts = defaultdict(lambda: defaultdict(int))

# Get unique connector words
unique_connectors = deutsch_stat_df["Connector Token"].unique()

# Iterate over tokens and parsed text
for tokens, parsed_text in zip(deutsch_tokens, deutsch_parsed_text):
    for i, token in enumerate(tokens):
        if token in unique_connectors:
            identifier = parsed_text[i]
            token_identifier_counts[token][identifier] += 1

# Print the counts for each special token and its corresponding identifiers
for token, identifier_counts in token_identifier_counts.items():
    print(f"Special Token: {token}")
    for identifier, count in identifier_counts.items():
        print(f"Identifier: {identifier}, Count: {count}")
token_identifier_counts

Special Token: und
Identifier: 1, Count: 154
Identifier: 0, Count: 363
Identifier: 8, Count: 7
Identifier: 3, Count: 3
Identifier: 16, Count: 1
Special Token: dessen
Identifier: 0, Count: 6
Identifier: 13, Count: 1
Identifier: 12, Count: 1
Special Token: mit
Identifier: 0, Count: 222
Special Token: zu
Identifier: 0, Count: 363
Identifier: 15, Count: 6
Special Token: da
Identifier: 0, Count: 30
Identifier: 7, Count: 3
Special Token: es
Identifier: 0, Count: 232
Identifier: 1, Count: 1
Special Token: inzwischen
Identifier: 0, Count: 9
Identifier: 11, Count: 1
Special Token: auch
Identifier: 0, Count: 180
Identifier: 1, Count: 21
Identifier: 6, Count: 5
Identifier: 2, Count: 1
Identifier: 29, Count: 1
Special Token: als
Identifier: 0, Count: 137
Identifier: 11, Count: 9
Identifier: 16, Count: 1
Special Token: noch
Identifier: 0, Count: 120
Identifier: 1, Count: 2
Special Token: aber
Identifier: 2, Count: 59
Identifier: 1, Count: 1
Identifier: 3, Count: 7
Identifier: 0, Count: 9
Identifier

defaultdict(<function __main__.<lambda>()>,
            {'und': defaultdict(int, {1: 154, 0: 363, 8: 7, 3: 3, 16: 1}),
             'dessen': defaultdict(int, {0: 6, 13: 1, 12: 1}),
             'mit': defaultdict(int, {0: 222}),
             'zu': defaultdict(int, {0: 363, 15: 6}),
             'da': defaultdict(int, {0: 30, 7: 3}),
             'es': defaultdict(int, {0: 232, 1: 1}),
             'inzwischen': defaultdict(int, {0: 9, 11: 1}),
             'auch': defaultdict(int, {0: 180, 1: 21, 6: 5, 2: 1, 29: 1}),
             'als': defaultdict(int, {0: 137, 11: 9, 16: 1}),
             'noch': defaultdict(int, {0: 120, 1: 2}),
             'aber': defaultdict(int, {2: 59, 1: 1, 3: 7, 0: 9, 6: 2}),
             'auf': defaultdict(int, {0: 179}),
             'zumal': defaultdict(int, {7: 3, 16: 1}),
             'um': defaultdict(int, {0: 70, 15: 16, 26: 1}),
             'deshalb': defaultdict(int, {0: 2, 12: 8}),
             'wenn': defaultdict(int, {10: 49, 11: 4, 0: 2, 6: 11,

In [159]:
# Create DataFrame
df_dict = {}
for token, values in token_identifier_counts.items():
    identifiers = {}
    for identifier, count in values.items():
        identifiers[identifier] = int(count)
    df_dict[token] = identifiers
stats_df = pd.DataFrame.from_dict(df_dict, orient='index')

# Fill NaN values with 0
stats_df = stats_df.fillna(0)
stats_df = stats_df.astype(int) 

# Export to plain text file
with open('Labels_stats(Connector ---> Relation).txt', 'w') as f:
    f.write(stats_df.to_string(index=True))
    
stats_df

1    0   8   3   16  13  12  15  7   11  ...  10  17  14  31  \
und          154  363   7   3   1   0   0   0   0   0  ...   0   0   0   0   
es             1  232   0   0   0   0   0   0   0   0  ...   0   0   0   0   
auch          21  180   0   0   0   0   0   0   0   0  ...   0   0   0   0   
noch           2  120   0   0   0   0   0   0   0   0  ...   0   0   0   0   
aber           1    9   0   7   0   0   0   0   0   0  ...   0   0   0   0   
...          ...  ...  ..  ..  ..  ..  ..  ..  ..  ..  ...  ..  ..  ..  ..   
z.             0    0   0   0   0   0   0   0   0   0  ...   0   0   0   0   
nachdem        0    0   0   0   0   0   0   0   0   0  ...   0   0   0   0   
desto          0    0   0   0   0   0   0   0   0   0  ...   0   0   0   0   
andernfalls    0    0   0   0   0   0   0   0   0   0  ...   0   0   0   0   
anstatt        0    0   0   0   0   0   0   0   0   0  ...   0   0   0   0   

             9   30  5   22  18  25  
und           0   0   0   0   0   0  
es            0   0   0   0   0   0  
auch          0   0   0   0   0   0  
noch          0   0   0   0   0   0  
aber          0   0   0   0   0   0  
...          ..  ..  ..  ..  ..  ..  
z.            1   0   0   0   0   0  
nachdem       0   0   2   0   0   0  
desto         0   0   0   2   0   0  
andernfalls   0   0   0   0   1   0  
anstatt       0   0   0   0   0   1  

[103 rows x 24 columns]

# Parsing Czech text files

In [113]:
def clean_dataframe(df):
    # Remove the columns with all nan values
    positionings_cz_cleaned = df.dropna(axis=1, how='all')
    # only select explicit connectors 
    positionings_cz_cleaned = positionings_cz_cleaned[positionings_cz_cleaned.iloc[:, 0] == "Explicit"].reset_index(drop=True)
    # only select and rename the 3 columns we are concerned with {1:offset, 7:connector word, 8: relation Label}
    positionings_cz_cleaned = positionings_cz_cleaned[[1,7,8]]
    positionings_cz_cleaned.rename(columns={1: "DcOffset", 7: "DcRaw", 8:"Label1"}, inplace=True)
    # Drop rows where DcOffset or DcRaw is not present
    positionings_cz_cleaned = positionings_cz_cleaned[(positionings_cz_cleaned['DcOffset'] != '') & (positionings_cz_cleaned['DcRaw'] != '')]
    return positionings_cz_cleaned

In [114]:
df = pd.read_csv("./Czech_data_folder/data/column/gold/03/mf920922_016",delimiter='|', header=None, error_bad_lines=False)
positionings_cz_cleaned = clean_dataframe(df)
positionings_cz_cleaned

/var/folders/ff/32yqt2f51gl_x3n8z960mc2r0000gn/T/ipykernel_923/823891584.py:1: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  df = pd.read_csv("./Czech_data_folder/data/column/gold/03/mf920922_016",delimiter='|', header=None, error_bad_lines=False)
b'Skipping line 2: expected 44 fields, saw 46\n'


DcOffset   DcRaw                                    Label1
0    342..348  přitom  Expansion.Level-of-detail.Arg2-as-detail
1  1172..1177   proto                  Contingency.Cause.Result
2  1076..1080    však      Comparison.Concession.Arg2-as-denier
3  1398..1399       a                     Expansion.Conjunction
4  1671..1676   spíše      Expansion.Substitution.Arg2-as-subst

In [148]:
# Iterate over all CSV files in every folder and parse the corresponding file in the raw text
directory = './Czech_data_folder/data/column/gold'
for root, dirs, files in os.walk(directory):
    # Iterate over all files in the current directory
    empty_files_count = 0
    for file in files:
        if file == '.DS_Store':
            continue
        # Join the current directory path with the file name to get the full file path
        file_path = os.path.join(root, file)
        print(file_path)
        #positionings_cz = pd.read_csv(file_path, delimiter='|', header=None, on_bad_lines='skip')
        with open(file_path, 'r', encoding='utf-8') as file:
            text = file.read()
            if text == "":
                empty_files_count += 1
                continue
            # Split the string into rows based on newline character
            rows = text.strip().split('\n')
            # Split each row into columns based on the delimiter '|'
            data = [row.split('|') for row in rows]
            positionings_cz = pd.DataFrame(data)
        positionings_cz_cleaned = clean_dataframe(positionings_cz) 
        
        # same processing like we did for the English
        result_cz = splitting_multiple_offsets(positionings_cz_cleaned, is_cz= True)
        #Apply the function to each row and concatenate the results
        new_rows = []
        for _, row in result_cz.iterrows():
            new_rows.extend(break_down_row(row, is_cz = True))
            
        # Create a new DataFrame with the modified rows
        splitted_rows_cz = pd.DataFrame(new_rows)
        # Reset index
        splitted_rows_cz.reset_index(drop=True, inplace=True)
        positionings_cz_cleaned = replace_splitted_rows(positionings_cz_cleaned, splitted_rows_cz,is_cz=True)
        
        # Get the corresponding raw text file in the 
        raw_file_path = file_path.replace('gold', 'raw')
        print(raw_file_path)
        with open(raw_file_path, 'r', encoding='utf-8') as file:
            text = file.read()
            # get the offsets- labels list of tuples
            connector_offsets_label_cz = list(zip(positionings_cz_cleaned['DcOffset'], positionings_cz_cleaned['Label1'].str.split('.').str[-1]))
            print(connector_offsets_label_cz)
            print(positionings_cz_cleaned)
            parsed,tokens = parse_text(text, connector_offsets_label_cz)
            print(parsed)
            print(tokens)
            for i, num in enumerate(parsed):
                if num != 0:
                    print(tokens[i])
            print(positionings_cz_cleaned)

./Czech_data_folder/data/column/gold/03/ln95045_002
./Czech_data_folder/data/column/raw/03/ln95045_002
[('190..191', 'Conjunction'), ('488..489', 'Conjunction'), ('521..527', 'Contrast'), ('610..611', 'Conjunction')]
   DcOffset   DcRaw                 Label1
0  190..191       a  Expansion.Conjunction
1  488..489       a  Expansion.Conjunction
2  521..527  naopak    Comparison.Contrast
3  610..611       a  Expansion.Conjunction
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
['Saldo', 'zahraničního', 'obchodu', 'se', 'loni', 'propadlo', 'do', 'pasívaGRAFPraha', 'Obrat', 'zahraničního', 'obchodu', 'se', 'loni', 'zvýši

      DcOffset    DcRaw                                    Label1
0     753..758    totiž  Expansion.Level-of-detail.Arg1-as-detail
1     809..810        :  Expansion.Level-of-detail.Arg2-as-detail
2   1275..1276        a                     Expansion.Conjunction
3   1532..1536     však                       Comparison.Contrast
4   1441..1444      kdy                  Contingency.Cause.Reason
5   1983..1988    totiž                  Contingency.Cause.Reason
6   2616..2620     také                     Expansion.Conjunction
7   2788..2795  protože                  Contingency.Cause.Reason
8   3144..3148     tedy                  Contingency.Cause.Reason
9   3262..3269  protože                  Contingency.Cause.Reason
10  3306..3309      -li        Contingency.Condition.Arg2-as-cond
11  3370..3374     však                       Comparison.Contrast
12  3416..3417        a                     Expansion.Conjunction
13  3562..3566     tedy  Expansion.Level-of-detail.Arg1-as-detail
14    136.

./Czech_data_folder/data/column/raw/03/mf930709_118
[('125..130', 'Result'), ('400..404', 'Result'), ('440..441', 'Conjunction'), ('711..712', 'Conjunction'), ('775..778', 'Arg2-as-cond'), ('886..887', 'Conjunction'), ('888..893', 'Condition+SpeechAct'), ('1174..1175', 'Conjunction'), ('1485..1488', 'Arg2-as-cond'), ('1786..1789', 'Conjunction'), ('2040..2041', 'Conjunction'), ('2042..2049', 'Reason'), ('2321..2322', 'Conjunction'), ('2633..2634', 'Conjunction'), ('2727..2731', 'Reason'), ('3054..3057', 'Arg2-as-goal'), ('3085..3086', 'Conjunction'), ('3198..3199', 'Conjunction'), ('3379..3380', 'Conjunction'), ('3547..3552', 'Result'), ('3578..3579', 'Conjunction'), ('3604..3607', 'Arg2-as-goal'), ('3931..3936', 'Result'), ('3822..3826', 'Equivalence'), ('2161..2167', 'Reason'), ('2168..2170', 'Reason'), ('3758..3760', 'Arg2-as-cond'), ('3761..3767', 'Arg2-as-cond'), ('3768..3770', 'Arg2-as-cond'), ('4095..4096', 'Arg2-as-denier'), ('4097..4099', 'Arg2-as-denier')]
      DcOffset    D

[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 0, 10, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 12, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 7, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

24  2528..2531      tak      Comparison.Concession.Arg2-as-denier
hey
Profit [('193..194', 'Reason+Belief'), ('222..223', 'Conjunction'), ('258..259', 'Conjunction'), ('341..342', 'Arg2-as-detail'), ('403..407', 'Contrast'), ('491..492', 'Conjunction'), ('559..563', 'Arg2-as-denier'), ('764..765', 'Arg2-as-detail'), ('862..867', 'Result'), ('1152..1157', 'Result'), ('958..963', 'Arg2-as-cond'), ('1092..1099', 'Reason'), ('1464..1465', 'Conjunction'), ('1959..1960', 'Conjunction'), ('3000..3001', 'Conjunction'), ('4037..4038', 'Conjunction'), ('4227..4234', 'Reason'), ('885..889', 'Arg2-as-denier'), ('905..908', 'Arg2-as-denier'), ('3176..3178', 'Arg2-as-subst'), ('3233..3239', 'Arg2-as-subst'), ('683..686', 'Result'), ('687..692', 'Result'), ('2526..2527', 'Arg2-as-denier'), ('2528..2531', 'Arg2-as-denier')]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 0,

...

./Czech_data_folder/data/column/raw/03/ln95048_016
[('630..638', 'Arg1-as-denier'), ('941..945', 'Arg2-as-denier'), ('1368..1369', 'Conjunction'), ('2215..2220', 'Conjunction'), ('2210..2214', 'Reason+Belief'), ('337..338', 'Reason'), ('339..341', 'Reason'), ('348..353', 'Reason'), ('348..354', 'Reason'), ('355..357', 'Reason'), ('1130..1131', 'Arg2-as-denier'), ('1132..1138', 'Arg2-as-denier')]
      DcOffset     DcRaw                                  Label1
0     630..638  přestože    Comparison.Concession.Arg1-as-denier
1     941..945      však    Comparison.Concession.Arg2-as-denier
2   1368..1369         a                   Expansion.Conjunction
3   2215..2220     navíc                   Expansion.Conjunction
4   2210..2214      když  Contingency.Cause+Belief.Reason+Belief
5     337..338         a                Contingency.Cause.Reason
6     339..341        to                Contingency.Cause.Reason
7     348..353     proto                Contingency.Cause.Reason
8     348..354  

./Czech_data_folder/data/column/raw/03/ln94209_52
[('199..204', 'Arg2-as-cond'), ('583..589', 'Arg2-as-denier'), ('765..772', 'Contrast'), ('1321..1325', 'Disjunction')]
     DcOffset    DcRaw                                Label1
0    199..204    kdyby    Contingency.Condition.Arg2-as-cond
1    583..589   přitom  Comparison.Concession.Arg2-as-denier
2    765..772  zatímco                   Comparison.Contrast
3  1321..1325     nebo                 Expansion.Disjunction
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 10, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0

[('121..128', 'Synchronous'), ('941..948', 'Precedence'), ('1059..1064', 'Conjunction'), ('2004..2005', 'Arg2-as-detail'), ('1972..1973', 'Conjunction'), ('2279..2280', 'Conjunction'), ('3041..3042', 'Conjunction'), ('3138..3141', 'Arg1-as-denier'), ('2321..2325', 'Arg2-as-denier'), ('2512..2516', 'Arg2-as-denier'), ('2734..2738', 'Arg2-as-denier'), ('2746..2749', 'Arg2-as-denier'), ('3302..3303', 'Arg2-as-denier'), ('3304..3307', 'Arg2-as-denier'), ('3308..3312', 'Arg2-as-denier')]
      DcOffset    DcRaw                                    Label1
0     121..128  zatímco                      Temporal.Synchronous
1     941..948  později          Temporal.Asynchronous.Precedence
2   1059..1064    navíc                     Expansion.Conjunction
3   2004..2005        :  Expansion.Level-of-detail.Arg2-as-detail
4   1972..1973        a                     Expansion.Conjunction
5   2279..2280        a                     Expansion.Conjunction
6   3041..3042        a                     Expans

./Czech_data_folder/data/column/raw/03/ln95049_019
[('513..520', 'Synchronous'), ('536..537', 'Conjunction'), ('607..609', 'Arg2-as-denier'), ('610..615', 'Arg2-as-denier'), ('616..622', 'Arg2-as-denier')]
   DcOffset    DcRaw                                Label1
0  513..520  zároveň                  Temporal.Synchronous
1  536..537        a                 Expansion.Conjunction
2  607..609       na  Comparison.Concession.Arg2-as-denier
3  610..615    druhé  Comparison.Concession.Arg2-as-denier
4  616..622   straně  Comparison.Concession.Arg2-as-denier
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 11, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 2, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
['Uhde', 'pro', 'dohodu', 'o', 'katedrálePraha', 'Snad', 'jedině', 'rozumná', 'dohoda', 'respektující', 'fak

ValueError: invalid literal for int() with base 10: '855;862'

In [116]:
for i, num in enumerate(parsed):
    if num != 0:
        print(tokens[i])
positionings_cz_cleaned

a
jestliže
pokud
kdyby
jestliže
dokud
pokud


DcOffset    DcRaw                                Label1
0     350..351        a                 Expansion.Conjunction
1     800..801        a                 Expansion.Conjunction
2     989..994    ovšem  Comparison.Concession.Arg2-as-denier
3   1305..1310    přece              Contingency.Cause.Reason
4   1358..1359        a                 Expansion.Conjunction
..         ...      ...                                   ...
76  2135..2141   přitom  Comparison.Concession.Arg1-as-denier
77  3011..3012        a      Temporal.Asynchronous.Precedence
78  3013..3016      pak      Temporal.Asynchronous.Precedence
79  5563..5564        a                 Expansion.Conjunction
80  5565..5572  nakonec                 Expansion.Conjunction

[81 rows x 3 columns]

In [263]:
positionings_cz_cleaned

DcOffset       DcRaw  \
0                450..458    přestože   
1                869..876     nicméně   
2              1091..1100   popřípadě   
3              1650..1653         pak   
4              1298..1302        a to   
5              1534..1538        však   
6              1582..1587       totiž   
7              1687..1688           a   
8              2070..2075       a tím   
9              2137..2140         pak   
10             2647..2652       proto   
11             2488..2493       pokud   
12             2528..2535     později   
13             2891..2896       ovšem   
14             2949..2953        nebo   
15             3023..3028       pokud   
16  3452..3456;3608..3613  sice ovšem   
17             3730..3735       proto   
18             3602..3607       pokud   
19             3994..3999       pokud   

                                            Label1  
0             Comparison.Concession.Arg1-as-denier  
1                              Comparison.Contrast  
2                            Expansion.Disjunction  
3                         Contingency.Cause.Result  
4         Expansion.Level-of-detail.Arg2-as-detail  
5             Comparison.Concession.Arg2-as-denier  
6                         Contingency.Cause.Reason  
7                            Expansion.Conjunction  
8                         Contingency.Cause.Result  
9                         Contingency.Cause.Reason  
10                        Contingency.Cause.Result  
11              Contingency.Condition.Arg2-as-cond  
12                Temporal.Asynchronous.Succession  
13            Comparison.Concession.Arg2-as-denier  
14                           Expansion.Disjunction  
15              Contingency.Condition.Arg2-as-cond  
16            Comparison.Concession.Arg2-as-denier  
17                        Contingency.Cause.Result  
18              Contingency.Condition.Arg2-as-cond  
19  Contingency.Negative-condition.Arg2-as-negCond

# Parsing French Text files 

In [202]:
def process_text_with_conn_tag(tuple_list):
    article_token_list = []
    article_parsed_list = []
    
    for tup in tuple_list:
        french_text = tup[1]
        tokens = french_text.split()
        multi_conn_flag = 0
        processed_tokens = []
        conn_list = []
        print(tokens)
        for token in tokens:
            # single token case
            if "<CONN>" in token and "</CONN>" in token:
                string_between_tags = re.search(r'<CONN>(.*?)</CONN>', token).group(1)
                processed_tokens.append(string_between_tags)
                conn_list.append(1)
                print(f"single worded connector: {token}")
            # multiworded connector case
            elif "<CONN>" in token:
                text_after_tag = re.search(r'<CONN>(.*?)$', token).group(1)
                processed_tokens.append(text_after_tag)
                conn_list.append(1)
                multi_conn_flag = 1
                print(f"multi worded connector: {token}")
            # still itereating multiworded tokens
            elif multi_conn_flag == 1:
                # mark the end of the multiworded connectors
                if "</CONN>" in token:
                    multi_conn_flag = 0
                    text_before_tag = re.search(r'(.*?)</CONN>', token).group(1)
                    processed_tokens.append(text_before_tag)
                    conn_list.append(1)
                    print(f"multi worded connector: {token}")
                # intermediate connectors (connector length > 2)
                else:
                    print(f"large multi worded connector: {token}")
                    processed_tokens.append(token)
                    conn_list.append(1)
                
            else:
                print(f"normal token: {token}")
                processed_tokens.append(token)
                conn_list.append(0)
        article_token_list.append(processed_tokens)
        article_parsed_list.append(conn_list)
        print(processed_tokens)
        print(conn_list)
        print()
        
    return article_token_list, article_parsed_list

In [203]:
# Read the XML file
with open("french_corpus_validated.xml", "r", encoding="utf-8") as file:
    xml_data = file.read()

# Initialize lists to store all tokens and connectors
all_processed_tokens_list_french = []
all_conn_list_french = []

# Define regex patterns
article_pattern = re.compile(r'<ARTICLE id="(.*?)">(.*?)</ARTICLE>', re.DOTALL)
sent_pattern = re.compile(r'<SENT id="(.*?)">(.*?)</SENT>', re.DOTALL)
conn_pattern = re.compile(r'<CONN>(.*?)</CONN>')
# Find all articles
articles = re.findall(article_pattern, xml_data)

# Iterate over articles
for article_id, article_content in articles:
    # Find all sentences in the article
    sentences = re.findall(sent_pattern, article_content)
    #process samples of given article
    processed_tokens, conn_list = process_text_with_conn_tag(sentences)
    # appending the results in the all tokens and connectors list
    for inner_list in processed_tokens:
        all_processed_tokens_list_french.append(inner_list)
    for inner_list in conn_list:
        all_conn_list_french.append(inner_list)

['Dans', 'ce', 'groupe', 'diversifié', '(', 'transports', ',', 'textile', ',', 'télévision', ')', 'dont', 'la', 'devise', 'est', ',', 'selon', 'le', 'mot', 'du', 'PDG', ',', 'Mr', 'Jérôme', 'Seydoux', ',', '"', 'gagner', 'de', "l'", 'argent', ',', "c'", 'est', 'vertueux', '"', ',', "l'", 'activité', 'aérienne', 'a', 'dégagé', 'un', 'résultat', 'bénéficiaire', 'net', 'de', '729', 'millions', 'de', 'francs', ',', 'sur', 'un', 'total', 'consolidé', 'de', '913', 'millions', 'de', 'francs', '.']
normal token: Dans
normal token: ce
normal token: groupe
normal token: diversifié
normal token: (
normal token: transports
normal token: ,
normal token: textile
normal token: ,
normal token: télévision
normal token: )
normal token: dont
normal token: la
normal token: devise
normal token: est
normal token: ,
normal token: selon
normal token: le
normal token: mot
normal token: du
normal token: PDG
normal token: ,
normal token: Mr
normal token: Jérôme
normal token: Seydoux
normal token: ,
normal token:

normal token: pays
normal token: "
normal token: ,
normal token: a
normal token: ajouté
normal token: l'
normal token: agence
normal token: ,
normal token: estimant
normal token: que
normal token: ces
normal token: mesures
normal token: "
normal token: peuvent
normal token: être
normal token: qualifiées
normal token: avec
normal token: certitude
normal token: d'
normal token: état
normal token: d'
normal token: urgence
normal token: "
normal token: .
['"', 'Soucieuses', "d'", 'empêcher', 'des', 'manifestations', 'de', 'protestation', ',', 'les', 'autorités', 'albanaises', 'ont', 'mis', 'en', 'place', 'des', 'mesures', 'extrêmement', 'rigoureuses', 'de', 'contrôle', 'de', 'la', 'situation', 'dans', 'le', 'pays', '"', ',', 'a', 'ajouté', "l'", 'agence', ',', 'estimant', 'que', 'ces', 'mesures', '"', 'peuvent', 'être', 'qualifiées', 'avec', 'certitude', "d'", 'état', "d'", 'urgence', '"', '.']
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

normal token: étrangers
normal token: et
normal token: peuplée
normal token: surtout
normal token: de
normal token: Russes
normal token: ,
normal token: notamment
normal token: les
normal token: ouvriers
normal token: d'
normal token: une
normal token: usine
normal token: de
normal token: réparation
normal token: d'
normal token: avions
normal token: qui
normal token: lui
normal token: ont
normal token: exprimé
normal token: leur
normal token: soutien
normal token: ,
normal token: a
normal token: indiqué
normal token: un
normal token: porte
normal token: -
normal token: parole
normal token: officiel
normal token: lituanien
normal token: .
['Vendredi', ',', 'il', "s'", 'était', 'rendu', 'à', 'Shauliai', ',', 'une', 'ville', 'interdite', 'aux', 'étrangers', 'et', 'peuplée', 'surtout', 'de', 'Russes', ',', 'notamment', 'les', 'ouvriers', "d'", 'une', 'usine', 'de', 'réparation', "d'", 'avions', 'qui', 'lui', 'ont', 'exprimé', 'leur', 'soutien', ',', 'a', 'indiqué', 'un', 'porte', '-', 'pa

normal token: fait
normal token: particulière
normal token: .
['Car', 'la', 'situation', 'de', 'la', 'Lituanie', 'est', 'tout', 'à', 'fait', 'particulière', '.']
[1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]

['La', 'fièvre', 'indépendantiste', "s'", 'y', 'explique', 'en', 'grande', 'partie', 'par', 'le', 'fait', 'que', 'les', 'Lituaniens', 'sont', 'largement', 'majoritaires', '(', '80', '%', ')', 'dans', 'leur', 'République', '<CONN>et</CONN>', "qu'", 'elle', 'ne', 'fait', 'partie', 'de', "l'", 'URSS', ',', 'avec', 'les', 'deux', 'autres', 'Républiques', 'baltes', ',', 'que', 'depuis', 'peu', '.']
normal token: La
normal token: fièvre
normal token: indépendantiste
normal token: s'
normal token: y
normal token: explique
normal token: en
normal token: grande
normal token: partie
normal token: par
normal token: le
normal token: fait
normal token: que
normal token: les
normal token: Lituaniens
normal token: sont
normal token: largement
normal token: majoritaires
normal token: (
normal token: 80
no

normal token: Jalilabad
normal token: ,
normal token: qui
normal token: s'
normal token: était
normal token: déjà
normal token: insurgée
normal token: en
normal token: décembre
normal token: dernier
normal token: .
["L'", 'agence', 'rapporte', 'également', "qu'", 'à', 'Lenkoran', ',', 'où', 'la', 'radio', 'a', 'été', 'occupée', ',', 'de', 'même', 'que', "d'", 'autres', 'bâtiments', 'officiels', ',', '"', 'tout', 'le', 'pouvoir', 'est', 'passé', 'aux', 'mains', 'du', 'front', 'populaire', '"', 'et', 'que', 'la', 'situation', "s'", 'aggrave', 'aussi', 'dans', 'la', 'ville', 'proche', 'de', 'Jalilabad', ',', 'qui', "s'", 'était', 'déjà', 'insurgée', 'en', 'décembre', 'dernier', '.']
[0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]

['-', 'Les', 'pourparlers', 'sur', 'le', 'retrait', 'des', 'troupes', 'soviétiques', 'de', 'Tchécoslovaquie', 'devraient', 'commencer',

...

normal token: ne
normal token: seront
normal token: pas
normal token: perceptibles
normal token: "
normal token: avant
normal token: plusieurs
normal token: jours
normal token: "
normal token: ,
multi worded connector: <CONN>étant
large multi worded connector: donné
multi worded connector: que</CONN>
normal token: le
normal token: cours
normal token: d'
normal token: eau
normal token: traverse
normal token: plus
normal token: d'
normal token: un
normal token: millier
normal token: de
normal token: kilomètres
multi worded connector: <CONN>avant
multi worded connector: de</CONN>
normal token: pénétrer
normal token: en
normal token: territoire
normal token: irakien
normal token: .
['On', 'indique', 'que', 'les', 'conséquences', 'de', "l'", 'interruption', 'du', 'débit', 'fluvial', ',', 'qui', 'touchera', 'quelque', '1', ',', '5', 'million', "d'", 'agriculteurs', 'irakiens', 'utilisant', 'les', 'eaux', 'de', "l'", 'Euphrate', ',', 'ne', 'seront', 'pas', 'perceptibles', '"', 'avant', 'plusi

normal token: le
normal token: limogeage
normal token: de
normal token: Mr
normal token: Mazilu
normal token: du
normal token: CFSN
normal token: pour
normal token: "
normal token: atteinte
normal token: grave
normal token: à
normal token: la
normal token: politique
normal token: de
normal token: consensus
normal token: national
normal token: "
normal token: .
['Le', 'quotidien', 'Romania', 'Libera', 'a', 'ouvert', 'les', 'hostilités', 'samedi', 'en', 'réclamant', ',', 'en', 'première', 'page', ',', 'le', 'limogeage', 'de', 'Mr', 'Mazilu', 'du', 'CFSN', 'pour', '"', 'atteinte', 'grave', 'à', 'la', 'politique', 'de', 'consensus', 'national', '"', '.']
[0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]

["L'", 'ancien', 'rapporteur', 'de', 'la', 'commission', 'des', 'droits', 'de', "l'", 'homme', 'des', 'nations', 'unies', ',', 'qui', 'a', 'eu', 'les', 'pires', 'ennuis', 'pour', 'avoir', 'tenté', "d'", 'en', 'dénoncer', 'les', 'viola

normal token: ,
normal token: Valentin
normal token: Ceausescu
normal token: ,
normal token: fils
normal token: ainé
normal token: de
normal token: l'
normal token: ancien
normal token: dictateur
normal token: ,
normal token: a
normal token: été
normal token: présenté
normal token: samedi
normal token: ,
normal token: menottes
normal token: aux
normal token: mains
normal token: ,
normal token: à
normal token: la
normal token: télévision
normal token: roumaine
normal token: ,
multi worded connector: <CONN>de
large multi worded connector: même
multi worded connector: que</CONN>
normal token: plusieurs
normal token: proches
normal token: collaborateurs
normal token: de
normal token: son
normal token: père
normal token: .
['Par', 'ailleurs', ',', 'Valentin', 'Ceausescu', ',', 'fils', 'ainé', 'de', "l'", 'ancien', 'dictateur', ',', 'a', 'été', 'présenté', 'samedi', ',', 'menottes', 'aux', 'mains', ',', 'à', 'la', 'télévision', 'roumaine', ',', 'de', 'même', 'que', 'plusieurs', 'proches', 'c

normal token: à
normal token: ce
normal token: jour
normal token: ,
normal token: et
normal token: parmi
normal token: eux
normal token: Pierre
normal token: Durand
normal token: .
['Ils', 'sont', 'une', 'dizaine', 'à', "l'", 'avoir', 'fait', 'à', 'ce', 'jour', ',', 'et', 'parmi', 'eux', 'Pierre', 'Durand', '.']
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]

['Narcotique', ',', 'la', 'jument', 'du', 'champion', 'olympique', ',', 'appelée', 'sans', 'doute', 'à', 'succéder', 'un', 'jour', 'à', 'Jappeloup', ',', 'se', 'trouve', 'depuis', 'la', 'fin', 'octobre', 'au', 'haras', 'de', 'la', 'Gisloterie', ',', 'situé', 'en', 'plein', 'coeur', 'du', 'Calvados', ',', 'à', 'Sainte', '-', 'Marie', '-', "d'", 'elle', ',', '<CONN>pour</CONN>', 'y', 'subir', 'un', 'transfert', "d'", 'embryon', '.']
normal token: Narcotique
normal token: ,
normal token: la
normal token: jument
normal token: du
normal token: champion
normal token: olympique
normal token: ,
normal token: appelée
normal token: 

AttributeError: 'NoneType' object has no attribute 'group'

# Bracketing Annotation Parsing

## [ ] Tagging 

In [338]:
def tagging_connective_tokens(tokens_list, id_lists):
    tagged_tokens_list = []
    for i, id_list in enumerate(id_lists):
        tagged_tokens = []
        for j, id_ in enumerate(id_list):
            if id_ != 0:
                new_token = "[" + tokens_list[i][j] + "]"
                tagged_tokens.append(new_token)
            else:
                tagged_tokens.append(tokens_list[i][j])
        tagged_tokens_list.append(tagged_tokens)

    return tagged_tokens_list

In [339]:
def tagging_connective_tokens_relations(tokens_list, id_lists):
    tagged_tokens_list = []
    for i, id_list in enumerate(id_lists):
        tagged_tokens = []
        for j, id_ in enumerate(id_list):
            if id_ != 0:
                new_token = "[" + tokens_list[i][j] + "]"
                print(id_)
                relation = next((key for key, value in label_map.items() if value == id_), None)
                relation_token = "(" + relation + ")"
                tagged_tokens.append(new_token)
                tagged_tokens.append(relation_token)

            else:
                tagged_tokens.append(tokens_list[i][j])
        tagged_tokens_list.append(tagged_tokens)

    return tagged_tokens_list

In [427]:
# for Connective detection
train_tagged_tokens = tagging_connective_tokens(train_tokens_sentences, train_ids_sentences)
test_tagged_tokens = tagging_connective_tokens(test_tokens_sentences, test_ids_sentences)
dev_tagged_tokens = tagging_connective_tokens(dev_tokens_sentences, dev_ids_sentences)

In [240]:
# Convert tokens and ids to JSON lines files
output_file = 'train_connective_detection_tagging.jsonl'
convert_to_jsonl(train_tokens_sentences, train_tagged_tokens, output_file)

output_file = 'test_connective_detection_tagging.jsonl'
convert_to_jsonl(test_tokens_sentences, test_tagged_tokens, output_file)

output_file = 'dev_connective_detection_tagging.jsonl'
convert_to_jsonl(dev_tokens_sentences, dev_tagged_tokens, output_file)